In [1]:
from bps import base
import pandas as pd
import numpy as np
from us import states
import functools

import altair as alt

In [2]:
pd.set_option('display.max_rows', 200)
pd.set_option('display.max_columns', 50)

In [3]:
import imp
imp.reload(base)

<module 'bps.base' from '/Users/subin/Code/building-permits-survey/bps/base.py'>

In [59]:
import pathlib
cwd = pathlib.Path.cwd()
data_dir = cwd / 'data'

# Download data

In [4]:
west_dfs = [
    base.load_data(scale='place', time_scale='annual', region='west', year=year)
    for year in range(1980, 2019)
]

In [5]:
south_dfs = [
    base.load_data(scale='place', time_scale='annual', region='south', year=year)
    for year in range(1980, 2019)
]

In [6]:
midwest_dfs = [
    base.load_data(scale='place', time_scale='annual', region='midwest', year=year)
    for year in range(1980, 2019)
]

In [7]:
northeast_dfs = [
    base.load_data(scale='place', time_scale='annual', region='northeast', year=year)
    for year in range(1980, 2019)
]

In [8]:
data = pd.concat(west_dfs + south_dfs + midwest_dfs + northeast_dfs)

# Clean up/prepare data

In [9]:
data['Survey Date'].unique()

array(['8099', '\x1a', '8199', '8299', '8399', '8499', '8599', '8699',
       '8799', '8899', '8999', '9099', '9199', '9299', '9399', '9499',
       '9599', '9699', '9799', '9899', 1999, 2000, 2001, 2002, 2003, 2004,
       2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015,
       2016, 2017, 2018], dtype=object)

In [10]:
broken_dates_map = {
    '{:2d}99'.format(i): '19{:2d}'.format(i) for i in range(80, 99)
}
def fix_date(date):
    if date in broken_dates_map:
        return broken_dates_map[date]
    else:
        return date
data['Survey Date'] = data['Survey Date'].map(fix_date)

In [11]:
def get_state(state_code):
    if not np.isnan(state_code):
        state = states.lookup('{:02d}'.format(int(state_code)))
        if state:
            return state.abbr
    
data['State'] = data['State Code'].apply(get_state)

In [12]:
cbsa_2018 = data[
    (data['Survey Date'] == 2018)
][['Place Name', 'State', 'CBSA Code']].drop_duplicates()

In [13]:
cbsa_2018_dict = cbsa_2018.set_index(['Place Name', 'State'])['CBSA Code'].to_dict()

In [14]:
data['2018 CBSA'] = data.apply(
    lambda row: cbsa_2018_dict.get(
        (row['Place Name'], row['State'])
    ), axis=1
)

In [15]:
data['Survey Date'].unique()

array(['1980', '\x1a', '1981', '1982', '1983', '1984', '1985', '1986',
       '1987', '1988', '1989', '1990', '1991', '1992', '1993', '1994',
       '1995', '1996', '1997', '1998', 1999, 2000, 2001, 2002, 2003, 2004,
       2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015,
       2016, 2017, 2018], dtype=object)

In [16]:
data['Year'] = pd.to_datetime(data['Survey Date'], format='%Y', errors='coerce')

In [17]:
data['Population'] = data['Pop   '].str.strip().apply(lambda x: x if x else None).astype(float)

In [18]:
population_by_place = data.query('Year == 2018')[['Place Name', 'State', 'Population']].set_index(['Place Name', 'State'])['Population'].to_dict()

In [19]:
data['2018 Population'] = data[['Place Name', 'State']].apply(
    lambda row: population_by_place.get((row['Place Name'], row['State'])),
    axis=1
)

In [20]:
data[['Place Name', 'Population']].sort_values('Population', ascending=False).drop_duplicates().head()

Place Name  Population
1819          Bronx borough   8008278.0
1820       Brooklyn borough   8008278.0
2841  Staten Island borough   8008278.0
2685         Queens borough   8008278.0
2393      Manhattan borough   8008278.0

In [21]:
data['5-unit per 1000 population'] = data['5+ units Units'] / data['2018 Population'] * 1000

In [22]:
data.columns


Index(['Survey Date', 'State Code', '6-Digit ID', 'County Code', 'MSA/CMSA',
       'PMSA Code', 'Region Code', 'Division Code', 'Number of Months Rep',
       ' ', 'Place Name', ' Bldgs', '1-unit Units', '1-unit Value',
       '1-unit Bldgs', '2-units Units', '2-units Value', '2-units Bldgs',
       '3-4 units Units', '3-4 units Value', '3-4 units Bldgs',
       '5+ units Units', '5+ units Value', '5+ units Bldgs',
       '1-unit rep Units', '1-unit rep Value', '1-unit rep Bldgs',
       '2-units rep Units', '2-units rep Value', '2-units rep Bldgs',
       '3-4 units rep Units', '3-4 units rep Value', '3-4 units rep Bldgs',
       '5+ units rep Units', '5+ units rep Value', 'Place Code',
       'Central City', 'Zip Code', 'CSA CSA', 'CBSA Code', 'CSA Code',
       'Footnote Code', 'Census Place Code', 'FIPS Place Code',
       'FIPS MCD Code', 'Pop   ', 'State', '2018 CBSA', 'Year', 'Population',
       '2018 Population', '5-unit per 1000 population'],
      dtype='object')

In [61]:
id_cols = ['State Code', '6-Digit ID', 'County Code', 'CBSA Code']
def intmap(idx):
    if np.isnan(idx):
        return 99999
    else:
        return np.int(idx)
for id_col in id_cols:
    data[id_col] = data[id_col].map(intmap)
data.tail()

Survey Date  State Code  6-Digit ID  County Code  MSA/CMSA  PMSA Code  \
5572        2018          50      591000           15       NaN        NaN   
5573        2018          50      593000           23       NaN        NaN   
5574        2018          50      595000            3       NaN        NaN   
5575        2018          50      597000           27       NaN        NaN   
5576        2018          50      599000           27       NaN        NaN   

      Region Code  Division Code  Number of Months Rep             Place Name  \
5572          1.0            1.0                  12.0 NaN       Wolcott town   
5573          1.0            1.0                   0.0 NaN      Woodbury town   
5574          1.0            1.0                  12.0 NaN      Woodford town   
5575          1.0            1.0                  12.0 NaN     Woodstock town   
5576          1.0            1.0                  12.0 NaN  Woodstock village   

       Bldgs  1-unit Units  1-unit Value  1-unit Bldgs  2-units Units  \
5572     9.0           9.0      988200.0           0.0            0.0   
5573     4.0           4.0      984063.0           0.0            0.0   
5574     0.0           0.0           0.0           0.0            0.0   
5575     2.0           2.0      499572.0           0.0            0.0   
5576     1.0           1.0      249786.0           1.0            2.0   

      2-units Value  2-units Bldgs  3-4 units Units  3-4 units Value  \
5572            0.0            0.0              0.0              0.0   
5573            0.0            0.0              0.0              0.0   
5574            0.0            0.0              0.0              0.0   
5575            0.0            0.0              0.0              0.0   
5576       227254.0            0.0              0.0              0.0   

      3-4 units Bldgs  5+ units Units  5+ units Value  5+ units Bldgs  \
5572              0.0             0.0             0.0             9.0   
5573              0.0             0.0             0.0             0.0   
5574              0.0             0.0             0.0             0.0   
5575              0.0             0.0             0.0             2.0   
5576              0.0             0.0             0.0             1.0   

      1-unit rep Units  ...  2-units rep Units  2-units rep Value  \
5572               9.0  ...                0.0                0.0   
5573               0.0  ...                0.0                0.0   
5574               0.0  ...                0.0                0.0   
5575               2.0  ...                0.0                0.0   
5576               1.0  ...                2.0           227254.0   

      2-units rep Bldgs  3-4 units rep Units  3-4 units rep Value  \
5572                0.0                  0.0                  0.0   
5573                0.0                  0.0                  0.0   
5574                0.0                  0.0                  0.0   
5575                0.0                  0.0                  0.0   
5576                0.0                  0.0                  0.0   

      3-4 units rep Bldgs  5+ units rep Units  5+ units rep Value  Place Code  \
5572                  0.0                 0.0                 0.0         NaN   
5573                  0.0                 0.0                 0.0         NaN   
5574                  0.0                 0.0                 0.0         NaN   
5575                  0.0                 0.0                 0.0         NaN   
5576                  0.0                 0.0                 0.0         NaN   

      Central City  Zip Code CSA CSA CBSA Code  CSA Code  Footnote Code  \
5572                    5680     NaN     99999     999.0                  
5573                    5683     NaN     99999     999.0                  
5574                52019410     NaN     99999     999.0                  
5575                    5091     NaN     99999     999.0                  
5576                    5091     NaN     99999

In [24]:
df = data.set_index(['State', 'County Code', 'Year'])[['1-unit Units', '2-units Units', '3-4 units Units', '5+ units Units', 'Population']]
df = df.rename(mapper={'1-unit Units': '1 unit', '2-units Units': '2 units', '3-4 units Units': '3-4 units', '5+ units Units': '5+ units'}, axis=1)
df = df.sort_index()
df

1 unit  2 units  3-4 units  5+ units  Population
State County Code Year                                                        
AK    0           1992-01-01     0.0      0.0        0.0       0.0         NaN
                  1992-01-01     0.0      0.0        0.0       0.0         NaN
                  1992-01-01     0.0      0.0        0.0       0.0         NaN
                  1993-01-01     0.0      0.0        0.0       0.0         NaN
                  1993-01-01     0.0      0.0        0.0       0.0         NaN
...                              ...      ...        ...       ...         ...
NaN   99999       NaT            NaN      NaN        NaN       NaN         NaN
                  NaT            NaN      NaN        NaN       NaN         NaN
                  NaT            NaN      NaN        NaN       NaN         NaN
                  NaT            NaN      NaN        NaN       NaN         NaN
                  NaT            NaN      NaN        NaN       NaN         NaN

[738605 rows x 5 columns]

In [25]:
geo_info = data.set_index(['State', 'County Code'])[['Place Name', 'State Code', '6-Digit ID', '2018 Population']]
geo_info = geo_info.sort_index()
geo_info

Place Name  State Code  6-Digit ID  \
State County Code                                                              
AK    0            Balance of State-Part 1 Anchorage           2       69000   
      0            Balance of State-Part 2 Fairbanks           2       73000   
      0               Balance of State-Part 3 Juneau           2       77000   
      0            Balance of State-Part 1 Anchorage           2       69000   
      0            Balance of State-Part 2 Fairbanks           2       73000   
...                                              ...         ...         ...   
NaN   99999                                      NaN       99999       99999   
      99999                                      NaN       99999       99999   
      99999                                      NaN       99999       99999   
      99999                                      NaN       99999       99999   
      99999                                      NaN       99999       99999   

                   2018 Population  
State County Code                   
AK    0                        NaN  
      0                        NaN  
      0                        NaN  
      0                        NaN  
      0                        NaN  
...                            ...  
NaN   99999                    NaN  
      99999                    NaN  
      99999                    NaN  
      99999                    NaN  
      99999                    NaN  

[738605 rows x 4 columns]

In [26]:
df.to_csv(data_dir / 'units.csv')
geo_info.to_csv(data_dir / 'geo_info.csv')

In [60]:
# Now using CBSA
df1 = data.set_index(['CBSA Code', 'Year'])[['1-unit Units', '2-units Units', '3-4 units Units', '5+ units Units', 'Population']]
df1 = df1.rename(mapper={'1-unit Units': '1 unit', '2-units Units': '2 units', '3-4 units Units': '3-4 units', '5+ units Units': '5+ units'}, axis=1)
df1 = df1.sort_index()
df1 = df1.drop(labels=99999, level=0)
df1.to_csv(data_dir / 'units_byCBSA.csv')
df1

1 unit  2 units  3-4 units  5+ units  Population
CBSA Code Year                                                        
440       2003-01-01     0.0      0.0        0.0       0.0         NaN
          2003-01-01    16.0      0.0        0.0       0.0         NaN
          2003-01-01   110.0      0.0        0.0       0.0         NaN
          2003-01-01     0.0      0.0        0.0       0.0         NaN
          2003-01-01    12.0      0.0        0.0       0.0         NaN
...                      ...      ...        ...       ...         ...
49740     2018-01-01   294.0      0.0        0.0       0.0     25505.0
          2018-01-01    42.0      0.0        0.0       0.0     14287.0
          2018-01-01    15.0      0.0        0.0       0.0      2882.0
          2018-01-01   485.0      2.0        0.0       0.0     93064.0
          2018-01-01   175.0      2.0        0.0       0.0     60013.0

[171108 rows x 5 columns]

Determining granularity of useful substate info

In [28]:
data['Region Code'].unique()

array([nan,  4.,  3.,  2.,  1.])

In [29]:
len(data['PMSA Code'].unique())

97

In [30]:
len(data[data['PMSA Code'].isnull()])

403905

In [31]:
data[data['PMSA Code'].isnull()][' Bldgs'].sum()

17674354.0

In [32]:
data[data['PMSA Code'].notnull()][' Bldgs'].sum()

19127171.0

In [33]:
len(data['MSA/CMSA'].unique())

391

In [34]:
len(data['Place Name'].unique())

55691

In [35]:
data['Central City'].unique()

array([nan, ' ', '1', '0', 'C'], dtype=object)

In [36]:
data['CSA CSA'].unique()

array([ nan, 999., 412., 348., 488., 472., 260., 216., 292., 332., 749.,
       492., 102., 140., 482., 262., 500., 760., 222., 142., 290., 218.,
       194., 516., 380., 388., 340., 428., 548., 422., 202., 214., 122.,
       356., 496., 468., 174., 178., 336., 350., 406., 132., 508., 384.,
       318., 324., 768., 556., 480., 274., 298., 268., 172., 450., 120.,
       312., 152., 416., 588., 538., 234., 273., 192., 396., 316., 314.,
       400., 392., 304., 297., 206., 288., 204., 540., 154., 346., 352.,
       442., 372., 887., 176., 476., 426., 466., 688., 276., 294., 258.,
       452., 320., 112., 512., 420., 266., 220., 330., 474., 300., 696.,
       378., 244., 184., 338., 198., 534., 169., 432., 212., 566., 932.,
       360., 376., 252., 232., 118., 358., 554., 278., 408., 328., 560.,
       552., 438., 148., 160., 684., 104., 464., 532., 361., 816., 296.,
       430., 368., 558., 756., 564., 616.])

In [37]:
data[data['MSA/CMSA'].isnull()][' Bldgs'].sum()

15821429.0

In [38]:
data[' Bldgs'].sum()

36801525.0

In [39]:
data[data['MSA/CMSA'].notnull()][['1-unit Units', '2-units Units', '3-4 units Units', '5+ units Units']].sum().sum()

29696792.0

In [40]:
data[data['MSA/CMSA'].isnull()][['1-unit Units', '2-units Units', '3-4 units Units', '5+ units Units']].sum().sum()

23235241.0

In [62]:
len(data['6-Digit ID'].unique())

8170

In [64]:
cbsa_id_slice = data[['6-Digit ID', 'CBSA Code']].drop_duplicates()
cbsa_id_slice.head()

6-Digit ID  CBSA Code
0         500      99999
1        1000      99999
2        2000      99999
3        2100      99999
4        2300      99999

In [65]:
len(cbsa_id_slice)

20096

In [67]:
cbsa_id_slice1 = cbsa_id_slice[cbsa_id_slice['CBSA Code'] != 99999]
len(cbsa_id_slice1)

11977

In [68]:
state_cty = data[['State', 'County Code']].drop_duplicates()
len(state_cty)

3111

In [69]:
cbsa_id_slice2 = data[['State', 'County Code', 'CBSA Code']].drop_duplicates()
cbsa_id_slice2 = cbsa_id_slice2[cbsa_id_slice2['CBSA Code'] != 99999]
len(cbsa_id_slice2)

1242

In [70]:
cbsa_id_slice2

State  County Code  CBSA Code
1       AK           20      11260
10      AK           90      21820
14      AK          170      11260
45      AZ           21      38060
46      AZ           13      38060
...    ...          ...        ...
3055    PA            1      23900
3095    PA           55      16540
3136    PA           89      20700
3148    PA           37      14100
3444    PA           93      14100

[1242 rows x 3 columns]

In [71]:
# Do state & county codes ever map to two CBSA codes?
state_cty1 = cbsa_id_slice2.set_index(['State', 'County Code'])
state_cty1

CBSA Code
State County Code           
AK    20               11260
      90               21820
      170              11260
AZ    21               38060
      13               38060
...                      ...
PA    1                23900
      55               16540
      89               20700
      37               14100
      93               14100

[1242 rows x 1 columns]

In [73]:
state_cty1.groupby(['State', 'County Code']).count().max()

CBSA Code    3
dtype: int64

In [86]:
counts = state_cty1.groupby(['State', 'County Code']).count()
[(counts['CBSA Code'] == i).sum() for i in np.arange(1, 4)]

[1176, 30, 2]

In [74]:
cbsa_slice = data[['State', 'County Code', '6-Digit ID', 'CBSA Code']].drop_duplicates()
cbsa_slice = cbsa_slice[cbsa_slice['CBSA Code'] != 99999]
len(cbsa_slice)

12095

In [75]:
len(cbsa_slice) * 40

483800

In [76]:
cbsa_slice.groupby(['State', 'County Code', '6-Digit ID']).count().max()

CBSA Code    3
dtype: int64

In [87]:
counts1 = cbsa_slice.groupby(['State', 'County Code', '6-Digit ID']).count()
[(counts1['CBSA Code'] == i).sum() for i in np.arange(1, 4)]

[11356, 353, 11]

In [93]:
cbsa_slice1 = cbsa_slice.set_index(['State', 'County Code', '6-Digit ID']).groupby(['State', 'County Code', '6-Digit ID']).first()
cbsa_slice1

CBSA Code
State County Code 6-Digit ID           
AK    20          41000           11260
      90          177000          21820
                  181000          21820
                  425000          21820
      170         233000          11260
...                                 ...
WY    25          129000          16220
                  141000          16220
                  301000          16220
                  305000          16220
                  317000          16220

[11720 rows x 1 columns]

In [90]:
counts1

CBSA Code
State County Code 6-Digit ID           
AK    20          41000               1
      90          177000              1
                  181000              1
                  425000              1
      170         233000              1
...                                 ...
WY    25          129000              1
                  141000              1
                  301000              1
                  305000              1
                  317000              1

[11720 rows x 1 columns]

In [95]:
cbsa_slice2 = cbsa_slice1[counts1['CBSA Code'] == 1]
len(cbsa_slice2)

11356

In [111]:
cbsa_map = cbsa_slice2['CBSA Code'].to_dict()
cbsa_map.get(('AK', 20, 41000))
#cbsa_map

11260

In [99]:
data['CBSA Assign'] = data.apply(
    lambda row: cbsa_map.get(
        (row['State'], row['County Code'], row['6-Digit ID'])
    ), axis=1
)
data.head()

Survey Date  State Code  6-Digit ID  County Code  MSA/CMSA  PMSA Code  \
0        1980           2         500           20       NaN        NaN   
1        1980           2        1000           80       NaN        NaN   
2        1980           2        2000           90       NaN        NaN   
3        1980           2        2100           90       NaN        NaN   
4        1980           2        2300          110       NaN        NaN   

   Region Code  Division Code  Number of Months Rep        \
0          NaN            NaN                  12.0  12.0   
1          NaN            NaN                  12.0  12.0   
2          NaN            NaN                   0.0   0.0   
3          NaN            NaN                   0.0   0.0   
4          NaN            NaN                  12.0  12.0   

                           Place Name   Bldgs  1-unit Units  1-unit Value  \
0  ANCHORAGE CENSUS DIV * . . . . . .   809.0         809.0    71939809.0   
1  CORDOVA-MCCARTHY CENSUS DIV. * . .     9.0           9.0      528700.0   
2  FAIRBANKS. . . . . . . . . . . . .    75.0          75.0     5227779.0   
3  FAIRBANKS NORTH STAR BOROUGH . . .   293.0         293.0    13781072.0   
4  JUNEAU CENSUS DIV. * . . . . . . .   178.0         178.0    14181307.0   

   1-unit Bldgs  2-units Units  2-units Value  2-units Bldgs  3-4 units Units  \
0          56.0          112.0      6257397.0           20.0             72.0   
1           0.0            0.0            0.0            1.0              3.0   
2           0.0            0.0            0.0            0.0              0.0   
3          16.0           32.0      1415435.0            0.0              0.0   
4          16.0           32.0      1568373.0            4.0             15.0   

   3-4 units Value  3-4 units Bldgs  5+ units Units  5+ units Value  \
0        3744057.0             11.0            75.0       4558771.0   
1          80000.0              0.0             0.0             0.0   
2              0.0             11.0            98.0       7132164.0   
3              0.0              8.0            52.0       1929593.0   
4         582600.0              9.0            48.0       3840000.0   

   5+ units Bldgs  1-unit rep Units  ...  2-units rep Value  \
0           809.0             809.0  ...          6257397.0   
1             9.0               9.0  ...                0.0   
2             0.0               0.0  ...                0.0   
3             0.0               0.0  ...                0.0   
4           178.0             178.0  ...          1568373.0   

   2-units rep Bldgs  3-4 units rep Units  3-4 units rep Value  \
0               20.0                 72.0            3744057.0   
1                1.0                  3.0              80000.0   
2                0.0                  0.0                  0.0   
3                0.0                  0.0                  0.0   
4                4.0                 15.0             582600.0   

   3-4 units rep Bldgs  5+ units rep Units  5+ units rep Value  Place Code  \
0                 11.0                75.0           4558771.0         NaN   
1                  0.0                 0.0                 0.0         NaN   
2                  0.0                 0.0                 0.0         NaN   
3                  0.0                 0.0                 0.0         NaN   
4                  9.0                48.0           3840000.0         NaN   

   Central City  Zip Code CSA CSA CBSA Code CSA Code  Footnote Code  \
0           NaN       NaN     NaN     99999      NaN            NaN   
1           NaN       NaN     NaN     99999      NaN            NaN   
2           NaN       NaN     NaN     99999      NaN            NaN   
3           NaN       NaN     NaN     99999      NaN            NaN   
4           NaN       NaN     NaN     99999      NaN            NaN   

   Census Place Code  FIPS Place Code FIPS MCD Code Pop    State 2018 CBSA  \
0                NaN              NaN           NaN    Na

In [116]:
data['CBSA Assign'] = data['CBSA Assign'].map(intmap)

In [118]:
(data['CBSA Assign'].notnull()).sum()

738605

In [120]:
(data['CBSA Assign'] != 99999).sum()

287741

In [123]:
# Now try again
data2 = data.copy()
data2['CBSA Code'] = data2['CBSA Assign']
df2 = data2.set_index(['CBSA Code', 'Year'])[['1-unit Units', '2-units Units', '3-4 units Units', '5+ units Units', 'Population']]
df2 = df2.rename(mapper={'1-unit Units': '1 unit', '2-units Units': '2 units', '3-4 units Units': '3-4 units', '5+ units Units': '5+ units'}, axis=1)
df2 = df2.sort_index()
df2 = df2.drop(labels=99999, level=0)
#df2.to_csv(data_dir / 'units_byCBSA.csv')
df2

1 unit  2 units  3-4 units  5+ units  Population
CBSA Code Year                                                        
440       1992-01-01     1.0      0.0        0.0       0.0         NaN
          1992-01-01     6.0      0.0        0.0       0.0         NaN
          1992-01-01    35.0      0.0        0.0       0.0         NaN
          1992-01-01     1.0      0.0        0.0       0.0         NaN
          1992-01-01     3.0      0.0        4.0       0.0         NaN
...                      ...      ...        ...       ...         ...
49740     2018-01-01   294.0      0.0        0.0       0.0     25505.0
          2018-01-01    42.0      0.0        0.0       0.0     14287.0
          2018-01-01    15.0      0.0        0.0       0.0      2882.0
          2018-01-01   485.0      2.0        0.0       0.0     93064.0
          2018-01-01   175.0      2.0        0.0       0.0     60013.0

[287741 rows x 5 columns]

In [124]:
df2.to_csv(data_dir / 'units_byCBSA.csv')

# Make plots

In [41]:
cities = {
    'CA': [
        'San Francisco', 'Los Angeles', 'Irvine', 
        'Long Beach', 'Oakland', 'Sacramento', 'Glendale',
        'Berkeley', 'San Jose', 'Mountain View',
        'Palo Alto', 'Davis', 'Fremont', 'Dublin',
        'Emeryville',
        'Contra Costa Centre',
        'Walnut Creek',
        'San Mateo',
        'Redwood City',
        'Milpitas', 'Campbell', 'Santa Clara',
        'Cupertino',
        'Culver City',
        'Pasadena',
        'West Hollywood',
        'Santa Monica',
        'Santa Ana',
        'Newport Beach',
        'Inglewood',
        'Burbank',
        'Azusa',
    ],
    'TX': [
        'Dallas', 'Plano', 'Frisco', 'Richardson', 'Fort Worth', 'The Colony',
        'Allen', 'McKinney', 'Irving', 'Garland', 'Addison', 'Highland Park', 
        'University Park',
        
        'Houston', 'The Woodlands', 'Woodlands', 'Katy', 'Sugarland'
        
        'Austin',
    ],
    'WA': [
        'Seattle', 'Tacoma',
        'Kent', 'Seatac',
        'Bellevue', 'Redmond'
    ],
    # 'UT': ['Salt Lake City'],
    # 'NV': ['Las Vegas', 'Reno'],
    'CO': ['Denver', 'Boulder'],
    'OR': ['Portland'],
#     'NY': ['Hicksville'],
#     'CT': ['Stamford'],
    'IL': ['Chicago']
}

In [42]:
row_indices = [
    (data['Place Name'] == place) & (data['State'] == state)
    for state, places in cities.items()
    for place in places
]
to_plot = data[
    functools.reduce(lambda a, b: a | b, row_indices)
]

In [43]:
to_plot[
    to_plot['Place Name'] == 'Highland Park'
]

Empty DataFrame
Columns: [Survey Date, State Code, 6-Digit ID, County Code, MSA/CMSA, PMSA Code, Region Code, Division Code, Number of Months Rep,  , Place Name,  Bldgs, 1-unit Units, 1-unit Value, 1-unit Bldgs, 2-units Units, 2-units Value, 2-units Bldgs, 3-4 units Units, 3-4 units Value, 3-4 units Bldgs, 5+ units Units, 5+ units Value, 5+ units Bldgs, 1-unit rep Units, 1-unit rep Value, 1-unit rep Bldgs, 2-units rep Units, 2-units rep Value, 2-units rep Bldgs, 3-4 units rep Units, 3-4 units rep Value, 3-4 units rep Bldgs, 5+ units rep Units, 5+ units rep Value, Place Code, Central City, Zip Code, CSA CSA, CBSA Code, CSA Code, Footnote Code, Census Place Code, FIPS Place Code, FIPS MCD Code, Pop   , State, 2018 CBSA, Year, Population, 2018 Population, 5-unit per 1000 population]
Index: []

[0 rows x 52 columns]

In [44]:
hover = alt.selection_single(
    on='mouseover',
    nearest=True,
    empty='none'
)

plot = alt.Chart(to_plot).mark_line().encode(
    color='Place Name',
    x=alt.X('Year'),
    # y=alt.Y('5+ units Units'),
    y=alt.Y('5-unit per 1000 population'),
)

(
    plot
     .facet('2018 CBSA', columns=3)
     .resolve_legend(color='independent')
     .resolve_scale(color='independent', x='independent')
)

alt.FacetChart(...)

In [45]:
alt.Chart(to_plot).mark_line().encode(
    color='Place Name',
    x=alt.X('Year'),
    y='1-unit Units'
)

alt.Chart(...)

In [46]:
data[[
    'Survey Date',
    'Place Name',
    'State',
    '1-unit Units',
    '2-units Units', 
    '3-4 units Units',
    '5+ units Units',
    '5+ units Bldgs',
]].sort_values('5+ units Units', ascending=False).head(50).reset_index(drop=True)

Survey Date                          Place Name State  1-unit Units  \
0         2015                    Brooklyn borough    NY          43.0   
1         1986  LOS ANGELES. . . . . . . . . . . .    CA        1996.0   
2         1985  LOS ANGELES. . . . . . . . . . . .    CA        2588.0   
3         1983  DALLAS . . . . . . . . . . . . . .    TX        3732.0   
4         1988                         Los Angeles    CA        2088.0   
5         1982  HARRIS CO. UNINC. AREA . . . . . .    TX       14124.0   
6         1987  Los Angeles. . . . . . . . . . . .    CA        2324.0   
7         1985  DALLAS . . . . . . . . . . . . . .    TX        2522.0   
8         2014                             Houston    TX        5398.0   
9         2015                         Los Angeles    CA        1834.0   
10        1984  DALLAS . . . . . . . . . . . . . .    TX        2979.0   
11        1982  HOUSTON. . . . . . . . . . . . . .    TX        2672.0   
12        1983  AUSTIN . . . . . . . . . . . . . .    TX        2586.0   
13        2018                         Los Angeles    CA        2636.0   
14        1989                         Los Angeles    CA        2550.0   
15        1984  PHOENIX. . . . . . . . . . . . . .    AZ        5505.0   
16        2015                   Manhattan borough    NY           4.0   
17        1998                             Houston    TX        3978.0   
18        1986  SAN DIEGO. . . . . . . . . . . . .    CA        5546.0   
19        1985  MANHATTAN BOROUGH. . . . . . . . .    NY           0.0   
20        2015                      Queens borough    NY         171.0   
21        2008                    Brooklyn borough    NY           0.0   
22        1980  HOUSTON. . . . . . . . . . . . . .    TX        2789.0   
23        2017                         Los Angeles    CA        2360.0   
24        2006                         Los Angeles    CA        2421.0   
25        2015                              Dallas    TX        1455.0   
26        1985  PHOENIX. . . . . . . . . . . . . .    AZ        5685.0   
27        2016                         Los Angeles    CA        1796.0   
28        2007                             Chicago    IL         870.0   
29        2006                             Chicago    IL        1415.0   
30        1984  LOS ANGELES. . . . . . . . . . . .    CA        3521.0   
31        1986  DALLAS . . . . . . . . . . . . . .    TX        2142.0   
32        2005                               Miami    FL         107.0   
33        1983   HARRIS CO. (DUMMY). . . . . . . .    TX       11549.0   
34        2015                             Houston    TX        5112.0   
35        1983  PHOENIX. . . . . . . . . . . . . .    AZ        6224.0   
36        2015                             Seattle    WA         810.0   
37        1982  DALLAS . . . . . . . . . . . . . .    TX        2290.0   
38        2008                   Manhattan borough    NY           3.0   
39        2006                             Houston    TX        7503.0   
40        1982  SAN ANTONIO. . . . . . . . . . . .    TX        2112.0   
41        1981  HOUSTON. . . . . . . . . . . . . .    TX        3126.0   
42        1983  ARLINGTON. . . . . . . . . . . . .    TX        4020.0   
43        2007                   Manhattan borough    NY           6.0   
44        1985  SAN DIEGO. . . . . . . . . . . . .    CA        4686.0   
45        1983  SAN ANTONIO. . . . . . . . . . . .    TX        3542.0   
46        1990                         Los Angeles    CA        1895.0   
47        1983  HOUSTON. . . . . . . . . . . . . .    TX        3487.0   
48        1984  MESA . . . . . . . . . . . . . . .    AZ        2803.0   
49        2014                         Los Angeles    CA        1668.0   

    2-units Units  3-4 units Units  5+ units Units  5+ units Bldgs  
0           114.0            412.0         25457.0            43.0  
1           236.0            245.0         23368.0          1996.0  
2           130.0    

In [47]:
data.head()

Survey Date  State Code  6-Digit ID  County Code  MSA/CMSA  PMSA Code  \
0        1980           2         500           20       NaN        NaN   
1        1980           2        1000           80       NaN        NaN   
2        1980           2        2000           90       NaN        NaN   
3        1980           2        2100           90       NaN        NaN   
4        1980           2        2300          110       NaN        NaN   

   Region Code  Division Code  Number of Months Rep        \
0          NaN            NaN                  12.0  12.0   
1          NaN            NaN                  12.0  12.0   
2          NaN            NaN                   0.0   0.0   
3          NaN            NaN                   0.0   0.0   
4          NaN            NaN                  12.0  12.0   

                           Place Name   Bldgs  1-unit Units  1-unit Value  \
0  ANCHORAGE CENSUS DIV * . . . . . .   809.0         809.0    71939809.0   
1  CORDOVA-MCCARTHY CENSUS DIV. * . .     9.0           9.0      528700.0   
2  FAIRBANKS. . . . . . . . . . . . .    75.0          75.0     5227779.0   
3  FAIRBANKS NORTH STAR BOROUGH . . .   293.0         293.0    13781072.0   
4  JUNEAU CENSUS DIV. * . . . . . . .   178.0         178.0    14181307.0   

   1-unit Bldgs  2-units Units  2-units Value  2-units Bldgs  3-4 units Units  \
0          56.0          112.0      6257397.0           20.0             72.0   
1           0.0            0.0            0.0            1.0              3.0   
2           0.0            0.0            0.0            0.0              0.0   
3          16.0           32.0      1415435.0            0.0              0.0   
4          16.0           32.0      1568373.0            4.0             15.0   

   3-4 units Value  3-4 units Bldgs  5+ units Units  5+ units Value  \
0        3744057.0             11.0            75.0       4558771.0   
1          80000.0              0.0             0.0             0.0   
2              0.0             11.0            98.0       7132164.0   
3              0.0              8.0            52.0       1929593.0   
4         582600.0              9.0            48.0       3840000.0   

   5+ units Bldgs  1-unit rep Units  ...  2-units rep Units  \
0           809.0             809.0  ...              112.0   
1             9.0               9.0  ...                0.0   
2             0.0               0.0  ...                0.0   
3             0.0               0.0  ...                0.0   
4           178.0             178.0  ...               32.0   

   2-units rep Value  2-units rep Bldgs  3-4 units rep Units  \
0          6257397.0               20.0                 72.0   
1                0.0                1.0                  3.0   
2                0.0                0.0                  0.0   
3                0.0                0.0                  0.0   
4          1568373.0                4.0                 15.0   

   3-4 units rep Value  3-4 units rep Bldgs  5+ units rep Units  \
0            3744057.0                 11.0                75.0   
1              80000.0                  0.0                 0.0   
2                  0.0                  0.0                 0.0   
3                  0.0                  0.0                 0.0   
4             582600.0                  9.0                48.0   

   5+ units rep Value  Place Code  Central City Zip Code CSA CSA CBSA Code  \
0           4558771.0         NaN           NaN      NaN     NaN     99999   
1                 0.0         NaN           NaN      NaN     NaN     99999   
2                 0.0         NaN           NaN      NaN     NaN     99999   
3                 0.0         NaN           NaN      NaN     NaN     99999   
4           3840000.0         NaN           NaN      NaN     NaN     99999   

   CSA Code  Footnote Code  Census Place Code FIPS Place Code FIPS MCD Code  \
0       NaN            NaN                NaN             NaN           NaN   
1       NaN  